# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [363]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [3]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("WeatherPy_vacation.csv")

# Display sample data
vacation_df.head()

City ID            City Country  Max Temp Current Description      Lat  \
0        0       Tiruvalla      IN     74.03     overcast clouds   9.3833   
1        5       Hithadhoo      MV     81.12     overcast clouds  -0.6000   
2        7           Qeshm      IR     73.29       broken clouds  26.9581   
3        9  Port Elizabeth      ZA     70.32           clear sky -33.9180   
4       15      Georgetown      MY     79.23          few clouds   5.4112   

        Lng       Hotel Name  
0   76.5667         Victoria  
1   73.0833      Pebbles Inn  
2   56.2719      هتل آپادانا  
3   25.5701  Waterford Hotel  
4  100.3354   Page 63 hostel

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [4]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country", "Current Description"]
)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [7]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"] == "Olinda"]
vacation_end = vacation_df.loc[vacation_df["City"] == "Olinda"]
vacation_stop1 = vacation_df.loc[vacation_df["City"] == "Sao Jose Da Coroa Grande"]
vacation_stop2 = vacation_df.loc[vacation_df["City"] == "Maragogi"]
vacation_stop3 = vacation_df.loc[vacation_df["City"] == "Pitimbu"]

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [9]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start, vacation_stop1, vacation_stop2, vacation_stop3, vacation_end])

# Display sample data
itinerary_df

City ID                      City Country  Max Temp Current Description  \
37       157                    Olinda      BR     80.33    scattered clouds   
73       305  Sao Jose Da Coroa Grande      BR     77.54     overcast clouds   
85       343                  Maragogi      BR     76.64          light rain   
137      554                   Pitimbu      BR     79.39     overcast clouds   
37       157                    Olinda      BR     80.33    scattered clouds   

        Lat      Lng         Hotel Name  
37  -8.0089 -34.8553        Fidji Motel  
73  -8.8978 -35.1478       Hotel do Sol  
85  -9.0122 -35.2225    Pousada Mariluz  
137 -7.4706 -34.8086  Pousada Brisa Mar  
37  -8.0089 -34.8553        Fidji Motel

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [11]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itinerary.
waypoints_df = itinerary_df[["Lng", "Lat"]].copy()

# Display sample data
waypoints_df

Lng     Lat
37  -34.8553 -8.0089
73  -35.1478 -8.8978
85  -35.2225 -9.0122
137 -34.8086 -7.4706
37  -34.8553 -8.0089

## Use GeoViews to create map that shows the four cities in the itinerary

In [332]:
# Configure the map plot by using the itinerary_df
waypoints_map = waypoints_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = itinerary_df["Max Temp"],
    scale = 2,
    alpha = 0.5,
    color = itinerary_df["City"]
)

# Display the map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (_color,_size)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [48]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [103]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the waypoints_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
display(params["waypoints"])
display(params["mode"])

# Not displaying params["apiKey"] to keep geoapify key concealed

'-8.0089,-34.8553|-8.8978,-35.1478|-9.0122,-35.2225|-7.4706,-34.8086|-8.0089,-34.8553'

'drive'

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [96]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing?"

# Make request and retrieve the JSON data by using the params dictionary
route_response = requests.get(base_url + "waypoints=" + str(params["waypoints"]) + "&mode=" + str(params["mode"]) + "&apiKey=" + str(params["apiKey"]))

# Convert the API response to JSON format
route_response = route_response.json()
route_response

{'features': [{'type': 'Feature',
   'properties': {'mode': 'drive',
    'waypoints': [{'location': [-34.8553, -8.0089], 'original_index': 0},
     {'location': [-35.1478, -8.8978], 'original_index': 1},
     {'location': [-35.2225, -9.0122], 'original_index': 2},
     {'location': [-34.8086, -7.4706], 'original_index': 3},
     {'location': [-34.8553, -8.0089], 'original_index': 4}],
    'units': 'metric',
    'distance': 463814,
    'distance_units': 'meters',
    'time': 22188.683,
    'legs': [{'distance': 131126,
      'time': 6491.335,
      'steps': [{'from_index': 0,
        'to_index': 10,
        'distance': 278,
        'time': 25.128,
        'instruction': {'text': 'Drive northwest on Avenida da Saudade.'}},
       {'from_index': 10,
        'to_index': 15,
        'distance': 120,
        'time': 11.059,
        'instruction': {'text': 'Bear left onto Rua Leúcio Marquês de Almeida.'}},
       {'from_index': 15,
        'to_index': 21,
        'distance': 275,
        'tim

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [178]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]
legs

[[[-34.855412, -8.008953],
  [-34.855583, -8.008599],
  [-34.855689, -8.008387],
  [-34.85579, -8.008101],
  [-34.855813, -8.008018],
  [-34.855827, -8.007946],
  [-34.855869, -8.007622],
  [-34.855912, -8.007262],
  [-34.85594, -8.007136],
  [-34.855978, -8.006956],
  [-34.856085, -8.006555],
  [-34.856182, -8.006469],
  [-34.856315, -8.006374],
  [-34.85648, -8.006299],
  [-34.856723, -8.006221],
  [-34.857071, -8.006154],
  [-34.857041, -8.006016],
  [-34.856967, -8.005679],
  [-34.8569, -8.005389],
  [-34.856877, -8.005292],
  [-34.85679, -8.004881],
  [-34.856549, -8.00374],
  [-34.856545, -8.003588],
  [-34.856535, -8.003494],
  [-34.856513, -8.003383],
  [-34.856507, -8.003324],
  [-34.856506, -8.003249],
  [-34.856527, -8.003181],
  [-34.856556, -8.003139],
  [-34.856627, -8.003093],
  [-34.856671, -8.003073],
  [-34.856721, -8.00307],
  [-34.856794, -8.003086],
  [-34.856848, -8.003109],
  [-34.856895, -8.003147],
  [-34.856919, -8.003177],
  [-34.856936, -8.003199],
  [-34.85

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [236]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for i in range(len(legs)):
    
    for j in range(len(legs[i])):
    
        longitude.append(legs[i][j][0])
        latitude.append(legs[i][j][1])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [241]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["Longitude"] = longitude
route_df["Latitude"] = latitude

# Display sample data
route_df.head()

Longitude  Latitude
0 -34.855412 -8.008953
1 -34.855583 -8.008599
2 -34.855689 -8.008387
3 -34.855790 -8.008101
4 -34.855813 -8.008018

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [365]:
# Configure the route path by using the GeoViews' Path function
route_path = route_df.hvplot.paths(
    "Longitude",
    "Latitude",
    frame_height = 700,
    frame_width = 500,
    color = "Red",
    geo = True,
    tiles = "OSM",
    line_width = 5,
    alpha = 2
)
route_path

:Overlay
   .Tiles.I :Tiles   [x,y]
   .Path.I  :Path   [Longitude,Latitude]

In [373]:
# Display a composed plot by using the route_map and route_path objects (not successfully overlaying?)
waypoints_map * route_path

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (_color,_size)
   .Tiles.II :Tiles   [x,y]
   .Path.I   :Path   [Longitude,Latitude]